# **Optimization of Machine Learning Algorithms through Bayesian optimization and Gaussian Processes**

Project for the "Information Theory and Inference" class, held by Prof. Michele Allegra at University of Padova during Academic Year 2023-2024,

by Erica Brisigotti & Ekaterina Chueva

## **The task: Tuning ML hyperparameters**

Machine Learning (ML) algorithms often require meticulous adjustment of learning and model hyperparameters, such as the learning rate, mini-batch size, and size of the learner: this process, often deemed a black magic, requires expert knowledge, or brute-force search. Automated methods that optimize algorithm performance for specific problems are thus highly sought after.

To authomatize the search, we view such tuning as the optimization of an unknown black-box function $f$ that quantifies the performance of the learning algorithm, which evaluation is expensive to perform. [2] For this reason, we'll be looking at black-box derivative-free global optimization techniques, which are often called **surrogate models**, because of the surrogate that they use to model the objective function $f$ and to decide where to evaluate. [3]

In this work, we adopt the Bayesian optimization framework, where the performance $f$ of the learning algorithm is modelled as a sample from a Gaussian Process (GP), since GPs have proven to be useful surrogate models for computer experiments.

A nice property of GPs is that the Gaussianity of the prior is mantained the posterior distribution as observations (i.e. results of running the learning algorithm with different hyperparameters) are observed.

Lastly, we want to highlight two traits that distinguish ML algorithms from other black-box optimizations:
- each function evaluation and its complexity can be rated either in terms of time or resources
- ML experiments are often run in parallel [2]

## **Introducting Bayesian optimization & Gaussian Processes**

### **Bayesian Optimization**
Bayesian optimization aims to find the maximum of a function $f$ on some bounded set $\mathcal{X} \subset \mathbb{R}^d$:
$$ \max_{x \in X}{f(\vec{x})} $$
To reach this goal:
- a statistical model is built for $f(\vec{x})$ through GP: this computation increases processing time, but is also the key step to guarantee a higher quanity decision
- the probabilistic model is then exploited to make decisions about the next point $\vec{x}_{n+1} \in \mathcal{X}$ in which to evaluate the function: such decision is made based on the type of **acquisition function** that is chosen
- all information available from the previous evaluation of $f$ is used to not rely only on the local properties of $f(\vec{x}_n)$

This procedure is able to find the minimum within few evaluations, which works well in problems, like this one, where evaluating the function $f$ is expensive to perform. [2]
The resulting model is best-suited for optimization over continuous domains $X$ of dimension $d \leq 20 $ [3].


Out of all the possible statistical models, we decide to focus on a Gaussian Process since  it's a non-parametric model (we are already working on tuning hyperparameters and prefer not to add another layer of complexity), and works with Gaussian functions, which are flexible and tractable. [1]

### **Gaussian Processes**

A Gaussian process (GP) is a non-parametric model obtained by kernelizing a version of Bayesian linear regression in which the weights have been marginalized away. 

The Gaussian Process GP $(\mu_0,k)$ is a non-parametric model that is fully characterized by:
- its **prior mean function** $\mu_0 : \mathcal{X} \rightarrow \mathbb{R} $ provides a possible offset of the samples from the GP. In practice, this function is set to a constant $\mu_0(\vec{x}) = \mu_0$ and inferred from data using other techniques. Such tecniques include ... [see section V-A]
- its positively defined **kernel** or covariance **function** $k: \mathcal{X} \times \mathcal{X} \rightarrow \mathbb{R} $ which controls the smoothness and amplitude of samples from the GP and dictates the structure of the response functions we can fit. Based on [1], we focus on stationary kernels, which are shift invariant. More specifically, we use [Matern kernels](https://en.wikipedia.org/wiki/Mat%C3%A9rn_covariance_function), which are a very flexible class of stationary kernels that are parameterized by a smoothness parameter $\nu>0$ and are differentiable $(\nu-1)$ times.

Given a finite collection of $n$ points $\{ \vec{x}_i\}_{i=1}^n$, we define the variables:
- $\{ f_i = f( \vec{x}_i) \}_{i=1}^n$ which represent the unknown function values
- $\{ y_i\}_{i=1}^n$ which represent the noisy observations

In GP, we assume that:
- $\vec{f} = \{ f_i \}_{i=1}^n $ are jointly gaussian
- $\vec{y} = \{ y_i\}_{i=1}^n$ are normally distributed given $\vec{f}$
    $$ \vec{y} \; | \vec{f}, \sigma^2 \sim \mathcal{N}(\vec{f} , \sigma^2\mathbb{I}) $$

resulting in the following **prior** distribution:
$$ \vec{f} \; | X \sim \mathcal{N}(\vec{m} , K) = p(\vec{f}) $$


where $ X = \{ \vec{x}_i\}_{i=1}^n $, $ K :  K_{i,j} = \{ k(x_i, x_j) \} $ is the covariance matrix, and $ \vec{m} : m_i = \mu_0(\vec{x}_i)$.

On the other hand, the **posterior** distribution is:
$$ f(\vec{x}) \; | D_n \sim \mathcal{N}(\mu_n(\vec{x}) , \sigma^2_n(\vec{x}) )  $$

where:
- $\vec{k}(\vec{x})$ is the vector of covariance terms between $\vec{x}$ and $ X = \{ \vec{x}_i\}_{i=1}^n $ 
- $ \mu_n(\vec{x}) = \mu_0(\vec{x}) + \vec{k}(\vec{x})^T \cdot (K + \sigma^2 \cdot \mathbb{I})^{-1} \cdot (\vec{y} - \vec{m}) $ 
- $ \sigma_n^2(\vec{x}) = k(x,x) - \vec{k}(\vec{x})^T \cdot (K + \sigma^2 \cdot \mathbb{I})^{-1} \cdot k(\vec{x}) $ 
- $\mu_n(\vec{x})$, $\sigma_n^2(\vec{x})$ represent, respectively, the model's prediction and uncertainty in the objective function at point $\vec{x}$, and are used to select the next query point $x_{n+1}$.

### **The acquisition functions**

There are different strategies to selecing the next query point $\vec{x}_{n+1}$ based on the posterior model: these different strategies correspond to different acquisition functions, which are all defined as the expected utility of a query point $\vec{x}$:
$$ \alpha(\vec{x}, \mathcal{D}_n ) = \mathbb{E}_\theta \mathbb{E}_{y | \vec{x}, \theta }  [U(\vec{x}, y, \theta)] $$
where the utility function $U: \mathbb{R}^d \times \mathbb{R} \times \Theta \rightarrow \mathbb{R} $ measures the quality of an experiment, consisting of an arbitrary query point $\vec{x}$, its corresponding function value $y = f(\vec{x})$, and a setting of the model hyperparameters $\theta$.

These acquisition functions, which correspond to different utility functions $U$, are carefully designed to trade off between **exploration** of the seach space and **exploitation** of current promising areas, and to also be cheap to evaluate or approssimate (compared to the objective function $f$).

## **Implementing Bayesian Optimization**

The following is a pseudo-code for our BO algorithm:

<img src="pseudo_code.png" width="800" align="center"/>

In [38]:
# first of all, we import all the libraries that we are going to use
import numpy as np
import scipy.optimize as opt
from scipy.stats import norm
import matplotlib.pyplot as plt
from numpy import random
import copy
import olympus
import pandas as pd

from sklearn.model_selection import GridSearchCV
from tensorflow.keras.datasets import mnist
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D
from tensorflow.keras.layers import MaxPooling2D
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Flatten
from tensorflow.keras.optimizers import SGD

seed = 12345
random.seed(seed=seed)
FROM_SCRATCH=False

### **Initializing the kernel and mean of the GP**




- for the mean, we choose a constant mean $\mu (\vec{x}) = \mu_0$
- for the correlation/kernel function is chosen to be one of the following 4 most used Matern kernels are:
    - the square exponential kernel corresponds to the limiting kernel for $\nu \rightarrow \infty$:
        $$ k_{sq-exp}(\vec{x}, \vec{x}^\prime) = \theta_0^2 \cdot \exp\left(-\frac{1}{2} r^2 \right) = \theta_0^2 \cdot \exp\left(-\frac{1}{2} (\vec{x}- 
            \vec{x}^\prime )^T \cdot 
            \begin{bmatrix} \theta^2_{1} & & \\ & \ddots & \\ & & \theta^2_{d} \end{bmatrix} 
            \cdot (\vec{x}- \vec{x}^\prime )  \right) = \theta_0^2 \cdot \exp\left(-\frac{1}{2} \sum_{i=1}^d \theta_i^2 (x_i - x_i^\prime)^2 \right) $$
    - the exponential kernel, or Matern-1, which corresponds to $\nu=1$
      $$ k_{Matern-1}(\vec{x}, \vec{x}^\prime) = \theta_0^2 \cdot \exp(- r) = \theta_0^2 \cdot \exp \left( - \sqrt{\sum_{i=1}^d \theta_i^2 (x_i - 
          x_i^\prime)^2 } \right) $$
    - the Matern-3, which corresponds to $\nu=3$
      $$ k_{Matern-3}(\vec{x}, \vec{x}^\prime) = \theta_0^2 \cdot (1+\sqrt{3} \; r) \cdot \exp(- \sqrt{3} r) = 
            \theta_0^2 \cdot \left( 1+\sqrt{3\sum_{i=1}^d \theta_i^2 (x_i - x_i^\prime)^2 } \right) \cdot \exp \left( - \sqrt{3 \sum_{i=1}^d \theta_i^2 
            (x_i - x_i^\prime)^2 } \right) $$
    - the Matern-5, which corresponds to $\nu=5$
      $$ k_{Matern-5}(\vec{x}, \vec{x}^\prime) = \theta_0^2 \cdot (1+\sqrt{5} \; r+\frac{5}{3}r^2) \cdot \exp(- \sqrt{5} \; r) =  \theta_0^2 \cdot \left( 
          1+ \sqrt{5 \sum_{i=1}^d \theta_i^2 (x_i - x_i^\prime)^2 } +\frac{5}{3} \sum_{i=1}^d \theta_i^2 (x_i - x_i^\prime)^2 \right) \cdot \exp \left( - 
          \sqrt{5 \sum_{i=1}^d \theta_i^2 (x_i - x_i^\prime)^2 } \right) $$
      
    We see that the Matern class is parameterized by an amplitude $\theta_0$ and by $d$ length scale hyperparameters $\{ \theta_i \}_{i=1}^d$, which we
    jointly denote as $\theta = \{ \theta_i \}_{i=0}^d$. Because these kernel/covariance functions have learnable length scale parameters, they are also
    known as Automatic Relevance Determination (ARD) kernels.

We have a total of $d+2$ hyperparameters: $ \theta = \{ \theta_i \} _{i=0}^d $ and $ \mu_0$ , which will later be optimized through Maximum Likelihood Estimation (MLE).

In [39]:
def correlation(x, x_prime, theta_0, theta, kernel_type):
    ''' 
    function that computes the correlation/kernel value between x and x_prime, based on:
    - parameters theta_0 (scalar) and theta (d-size numpy vector of the kernel)
    - the kernel_type of kernel selected, which must be one of ['squared-exponential', 'matern-1', 'matern-3', 'matern-5']
    '''
    r_sq = np.sum( (x - x_prime)**2 * theta**2 )
    r = np.sqrt(r_sq)
    
    if kernel_type == 'squared-exponential':
        return (theta_0**2*np.exp( -1/2*r_sq ))
    
    elif kernel_type == 'matern-1':
        return theta_0**2*np.exp( -1*r )
    
    elif kernel_type == 'matern-3':
        return theta_0**2*(1+np.sqrt(3)*r)*np.exp( -np.sqrt(3)*r )
    
    elif kernel_type == 'matern-5':
        return theta_0**2*(1+np.sqrt(5)*r+5/3*r_sq)*np.exp( -np.sqrt(5)*r )
    
    else:
        raise TypeError("wrong kernel type name")

In [40]:
def covariance_matrix(x_i, theta_0, theta, kernel_type, noise):
    '''
    function that computes the covariance matrix, and its inverse, of the input data x_i based on a correlation/kernel 
    specified by type (which must be one of ['squared-exponential', 'matern-1', 'matern-3', 'matern-5']) 
    and parametrized by theta_0 and theta
    '''
    K = np.zeros((np.shape(x_i)[0],np.shape(x_i)[0]))
    for i in range(np.shape(x_i)[0]):
        for j in range(i, np.shape(x_i)[0]):
            nn = [noise**2 if i==j else 0]
            k = correlation(x_i[i], x_i[j], theta_0, theta, kernel_type) + nn
            K[i][j] = k
            K[j][i] = k
    
    #this condition is here if we run on SingularMatrix error, so we see the parameters that caused the issue
    if np.linalg.det(K) ==0:
        print("noise:", noise)
        print(K)
        print('x[0], x[0]', correlation(x_i[0], x_i[0], theta_0, theta, kernel_type))
        print(correlation(x_i[0], x_i[1], theta_0, theta, kernel_type))
        print(correlation(x_i[1], x_i[0], theta_0, theta, kernel_type))
        print(correlation(x_i[1], x_i[1], theta_0, theta, kernel_type))
        print(correlation(x_i[2], x_i[2], theta_0, theta, kernel_type))
    K_inv = np.linalg.inv(K)
    return K, K_inv

### **Computing the log-likelihood**




To determine the hyperparameters $ \theta = \{ \theta_i \} _{i=0}^d $ of kernel and constant mean $\mu_0$ through Maximum Likelihood Estimation (MLE), we need to compute the log-likelihood of the posterior of the GP.

An interesting property of the GP model is that it provides an analytical expression for the marginal likelihood of the data (meaning that the unknown latent function f is marginalized out). The **log marginal likelihood** is:
$$ \log\left[ \; p(\vec{y} \;|\{\vec{x}\}_{i=1}^n) \right]  
=  -\frac{1}{2} (\vec{y} - \vec{m}_\theta)^T \cdot (K_\theta  + \sigma^2 \cdot \mathbb{I})^{-1} \cdot (\vec{y} - \vec{m})
   -\frac{1}{2} \log\left| K_\theta + \sigma^2 \cdot \mathbb{I} \right|  - \frac{n}{2} \log(2\pi)  $$
where the vector $\theta$ is agumented from $\theta = \{ \theta_i \}_{i=0}^d$ to $\theta = [ \theta_0, \theta_1, \dots, \theta_d, \mu_0, \sigma^2]$ and the covariance matrix $K_\theta$ now depends on the parameter/subscript $\theta$. We see that:
- the first term $-\frac{1}{2} (\vec{y} - \vec{m}_\theta)^T \cdot (K_\theta  + \sigma^2 \cdot \mathbb{I})^{-1} \cdot (\vec{y} - \vec{m})$ quantifies how well the model fits the data by applying the [Mahalanobis distance](https://en.wikipedia.org/wiki/Mahalanobis_distance) between the model predictions and the data;
- the second term $-\frac{1}{2} \log\left| K_\theta + \sigma^2 \cdot \mathbb{I} \right|$ quantifies the model complexity, by giving lower complexity penalties to smoother covariance matrices, which have smaller determinants
- the third term $- \frac{n}{2} \log(2\pi)$ is a linear function of the number of data points n, indicating that the likelihood of data tends to decrease with larger data sets.

As long as the kernel is differentiable with respect to its hyperparameters , the marginal likelihood can be differentiated and can therefore be optimized to obtain a maximum-likelihood or empirical Bayes estimate of the kernel parameters. We will be implementing Maximum Likelihood Estimation (MLE) to optimize the hyperparameters of the ML model.

In [41]:
def log_likelihood(x, x_i, y_i, kernel_type, d): #Returns the opposite of the Log-Likelihood, which must be optimized
    '''
    function that computes the log-likelihood
    the inputs x of the log likelihood:
    - x[0] is a coefficient related to noise
    - x[1] is the parameter theta_0 of the correlation/kernel function
    - x[2], ..., x[d+1] are the parameter theta of the correlation/kernel function (which match the dimensionality d of the input x_i)
    - x[d+2] is the parameter mu_0 of the constant mean function 
    '''
    KB, KB_inv = covariance_matrix(x_i, x[1], x[2:(d+2)], kernel_type, x[0])
    if (np.linalg.det(KB) <=0):
        ll = 0
    else:
        ll = (-0.5* np.log(np.linalg.det(KB))-0.5 * np.dot(np.transpose(y_i - x[d+2]), np.dot(KB_inv,(y_i - x[d+2])))-2*np.log(2*np.pi))
    return ll

### **Definining the constraints of the optimization**



We make sure that our hyperparameters $\theta = \{ \theta_i \} _{i=0}^d$ are positive since they have the meaning of amplitude, accordingly to the [documentation](https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.fmin_cobyla.html) of the minimization method we are going to use.

In [42]:
 # we want them all to be >=0 and particularly the noise >= 10*machine precision or 0.01 (to avoid singularity issues later on)
def constr1(x):
    #return (x[0]-10*np.finfo(float).eps)
    return (x[0]-0.01)

def constr2(x):
    return x[1]

def constr3(x):
    return x[2]

def constr4(x):
    return x[3]

def constr5(x):
    return x[4]

### **Finding the optimal hyparameters** 



We find the optimal hyperparameters of the GP through MSE by applying a [built-in minimization function](https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.fmin_cobyla.html) to the opposite of the log-likelihood.

In [43]:
def GP_param_optimizer(x_i, y_i, starting_points, show=False):
    '''
    function that computes the maximum of the log-likelihood by finding the minimumm in the opposite of the log-likelihood, through the
    scipy.optimize.fmin_cobyla function, and based on the inputs:
    - the starting points for the optimization starting_points, which correspond to
        - starting_points[0] is a coefficient related to noise
        - starting_points[1] is the parameter theta_0 of the correlation/kernel function
        - starting_points[2], ..., starting_points[d+1] are the parameter theta of the correlation/kernel function (and match the size d of input x_i)
        - starting_points[d+2] is the parameter mu_0 of the constant mean function
    '''
    # we invert the log-likelihood to be able to use minimization strategies to find its minimum, to obtain the optimized parameters (with the same order
    # and structure as the inputs)
    d = x_i.shape[1] 
    xopt = opt.fmin_cobyla(lambda x: -1*log_likelihood(x, x_i, y_i, kernel_type, d), starting_points, cons=[constr1, constr2, constr3, constr4, constr5])
    # we print the results of the optimization
    noise_opt, theta_0_opt, theta_opt, mu_0_opt = xopt[0], xopt[1], xopt[2:(d+2)], xopt[d+1]
    K_opt, K_opt_inv = covariance_matrix(x_i, theta_0_opt, theta_opt, kernel_type, noise_opt)
    show = False
    if show:
        print('the optimal noise parameter is ', noise_opt )
        print('the optimal correlation/kernel parameter theta_0 is', theta_0_opt )
        print('the optimal correlation/kernel parameters theta are ', theta_opt )
        print('the optimal constant mean parameter mu_0 is ', mu_0_opt )
        print('the resulting covariance matrix is', K_opt)
    show = True
    return noise_opt, theta_0_opt, theta_opt, mu_0_opt, K_opt, K_opt_inv

### **Executing the GP**




We can finally execute the GP with the optimized parameters to find the parameters:

$$ \mu_n(\vec{x}) = \mu_0(\vec{x}) + \vec{k}(\vec{x})^T \cdot (K + \sigma^2 \cdot \mathbb{I})^{-1} \cdot (\vec{y} - \vec{m}) $$
$$ \sigma_n^2(\vec{x}) = k(x,x) - \vec{k}(\vec{x})^T \cdot (K + \sigma^2 \cdot \mathbb{I})^{-1} \cdot k(\vec{x}) $$

of the posterior distribution for the test point $\vec{x}$:

$$ f(\vec{x}) \; | D_n \sim \mathcal{N}(\mu_n(\vec{x}) , \sigma^2_n(\vec{x}) )  $$

where:
- $\vec{k}(\vec{x})$ is the vector of covariance terms between the test point $\vec{x}$ and $ X = \{ \vec{x}_i\}_{i=1}^n $ 
- $\mu_n(\vec{x})$ represents the model's prediction in the objective function in test point $\vec{x}$
- $\sigma_n^2(\vec{x})$ represents the model's uncertainty in the objective function at point $\vec{x}$

Later on, in the acquisition function, we'll use $\mu_n(\vec{x})$ and $\sigma_n^2(\vec{x})$ to make predictions for the next point.


In [44]:
def GP_predict(x_i, x_new, y_i, kernel_type, starting_points, show=False):
    '''
    function that computes the parameters of the posterior of the GP for many potential test values x_new
    output parameters: 
    - vector of means of the posterior mu_n
    - vector of variances of the posterior sigma_n_sq
    - the best observed value tau
    '''

    # after computing the optimal parameters, we already have the inverse of the (already) noisy covariance matrix
    
    noise_opt, theta_0_opt, theta_opt, mu_0_opt, _, K_opt_inv = GP_param_optimizer(x_i, y_i, starting_points, show)

    mu_n = np.zeros(np.shape(x_new)[0])
    sigma_n_sq = np.zeros(np.shape(x_new)[0])
    for j in range(np.shape(x_new)[0]):
        k_xx = correlation(x_new[j], x_new[j], theta_0_opt, theta_opt, kernel_type)
        Ks = np.zeros(np.shape(x_i)[0])
        for k in range(np.shape(x_i)[0]):
            Ks[k] = correlation(x_new[j], x_i[k], theta_0_opt, theta_opt, kernel_type) 
        # we finally compute the mean
        mu_n[j] = mu_0_opt + np.dot(np.dot(Ks.T, K_opt_inv), (y_i - mu_0_opt*np.ones(len(y_i)) ))
        # and the variance of the posterior distribution
        sigma_n_sq[j] = k_xx - np.dot(np.dot(Ks.T, K_opt_inv), Ks)
    
    return mu_n, sigma_n_sq

### **Implementing the desired acquisition function**




Based on the outputs $\mu_n(\vec{x})$ and $\sigma_n^2(\vec{x})$ of the GP, we want to choose the next query point $\vec{x}_{n+1}$ based on a chosen acquisition function.

There are different approaches to designing acquisition functions:

- improvement-based policies favor points that are likely to improve upon an incumbent target $\tau$. One of the simplest strategies consists of computing the probability of improvement (PI) $\alpha_{PI} (\vec{x}, \mathcal{D}_n)$, which measures the probability that a point x leads to an improvement upon $\tau$ and is maximised to select the next query point. 

    $$ \alpha_{PI} (\vec{x}, \mathcal{D}_n) = P[\nu > \tau] = \Phi \left( \frac{\mu_n(\textbf{x}) - \tau}{\sigma_n(\textbf{x})} \right) $$

    where $\Phi$ is the standard normal cumulative distribution function. So, for this criteria, the utility function $U(\vec{x}, \nu, \theta) = \mathbb{I}
    [\nu > \tau]$ is an indicator of improvement and simply accumulates the posterior probability mass above $\tau$ at x. PI can work very well with known targets, but with unknown targets it tends towards exploitation.
  
    Therefore, for unknown targets, **expected improvement** (EI) strategies are implemented, which are based on a untility function $U(\vec{x}, \nu, \theta) = 
    (\nu - \tau) \cdot \mathbb{I}[\nu > \tau]$, which is positive only if there is improvement. Because $\nu$ is normally distributed, the expectation
    value can be computed analytically as:
  
    $$ \alpha_{EI} = (\mu_n(\textbf{x}) - \tau)\Phi\left( \frac{\mu_n(\textbf{x}) - \tau}{\sigma_n(\textbf{x})}\right) + \sigma_n(\textbf{x})\phi\left( 
        \frac{\mu_n(\textbf{x}) - \tau}{\sigma_n(\textbf{x})}\right) $$
    
    where $\phi$ is the standard normal probability density function, and $\tau = max_{i=1}^ny_i$ is adaptively set to the best observed value since the
    true target objective value is often unknown.

In [45]:
def expected_improvement(x_new, mu_n, sigma_n_sq, tau):
    ei = np.zeros(np.shape(x_new)[0])
    for j in range(np.shape(x_new)[0]):
        if sigma_n_sq[j] <=0:
            ei[j] = 0
        else:
            sigma_n = np.sqrt(sigma_n_sq[j])
            ei[j] = ((mu_n[j] - tau) * norm.cdf((mu_n[j] - tau)/sigma_n)) + (sigma_n * norm.pdf((mu_n[j] - tau)/sigma_n))
    return ei

- **optimistic policies** negotiate between exploration and exploitation through the upper confidence bound criterion: using the upper confidence for every
  query point $\vec{x}$ corresponds to effectively using a fixed probability best case scenario. In our case, we implement the Gaussian process upper
  confidence bound, which leads to these simple following equation:
  $$ \alpha_{UCB}(\vec{x}) = \mu_n(\vec{x}) + \beta_n \cdot \sigma_n(\vec{x}) $$ 
    where $\beta_n$ is a hyperparameter to be set. We choose the simplest case, consisting of a constant hyperparameter $\beta_n = \beta$, which is set to one of the following values, where the confidence interval is two-sided:


| value of $\beta$ | Confidence Level |
|----------------|----------------|
| 1 | 68% |
| 3 | 95% |
| 5 | 99.7% |

In [46]:
def optimistic(x_new, mu_n, sigma_n_sq, beta):
    '''
    function that computes a vector of upper confidence bounds, one for each test point in x_new based on the following parameters:
    - the posterior mean mu_n of the GP (vector as long as the number of test points in x_new)
    - the posterior variance sigma_n_sq of the GP (vector as long as the number of test points in x_new)
    - the confidence level value beta (scalar)
    '''
    ucb = np.zeros(np.shape(x_new)[0])
    for j in range(np.shape(x_new)[0]):
        if sigma_n_sq[j] <=0:
            ucb[j] = 0
        else:
            sigma_n = np.sqrt(sigma_n_sq[j])
            ucb[j] = mu_n[j] + beta*sigma_n
    return ucb

In [47]:
def acquisition_function(policy, x_i, x_new, y_i, kernel_type, starting_points, beta, show=False):
    '''
    function that computes the acquisition function based on the chosen policy
    - the maximum number of attempts max_attempt must be smaller than the number of test points x_mew
    '''
    
    mu_n, sigma_n_sq = GP_predict(x_i, x_new, y_i, kernel_type, starting_points, show)
    
    # if we want to use an improvement-based policy, we choose the 
    if policy == 'expected-improvement':
        tau = np.max(y_i)
        all_values = expected_improvement(x_new, mu_n, sigma_n_sq, tau)

    # if we want to use an optimistic-based policy
    elif policy == 'optimistic':
        all_values = optimistic(x_new, mu_n, sigma_n_sq, beta)
    
    # we find the next query point as the one which maximises the estimators
    next_one = x_new[np.argmax(all_values)]
    if show:
        plt.plot(all_values, '-', label = 'all test points')
        plt.plot(np.argmax(all_values),all_values[np.argmax(all_values)], '*', label = 'next point')
        plt.ylabel('expected improvement')
        plt.xlabel('test point')
        plt.legend()

    return next_one, np.argmax(all_values)

### **Implementing Bayesian Optimization** 
We finally implement Bayesian Optimization by iterating the selection of new points to find the global optima of the black box function $f$), to return the optimal ML hyperparameters as the point corresponding to the maximum of the target function.

In [48]:
def bayesian_optimization(policy, x_0, x_new, y_0, kernel_type, starting_points, n_BO_iteration, func, filename, beta=3, show=False, show_BO=False):
    '''
    function that computes bayesian optimization to find the optimal ML hyperparameter best_x, and the corresponding maximum accuracy best_y
    based on:
    - the chosen acquisition function policy
    - the randomly chosen initial points (ML hyperparamer values) x_0 and the corresponding accuracies y_0
    - the test points x_new
    - the chosen kernel type
    - the startint points starting_points for the MLE optimization of the GP hyperparameters
    - the maximum number of attempts max_attempt at finding a new query point (in acquisition_function) that hasn't been examined already
      (i.e. is not in x_i already, i.e. we don't already know the corresponding accuracy y_i)
    - the maximum number of Bayesian Optimization steps n_BO_iteration
    - the function to evaluate (i.e. our ML algorithm, which is a function only of the hyperparameters to tune)
    
    '''
    
    x_i = copy.copy(x_0)
    y_i = copy.copy(y_0)
    
    best_points = np.zeros((n_BO_iteration, x_i.shape[1]))
    values_best_points = np.zeros(n_BO_iteration)
    for n in range(n_BO_iteration):
        # we find the next query point
        next_one, index_to_delete = acquisition_function(policy, x_i, x_new, y_i, kernel_type, starting_points, beta, show)
        
        # we add the query point to the initial points
        print("Next chosen point is:", next_one, 'iteration: ', n)
        
        # we update our beliefs
        x_i = np.vstack([x_i, next_one])
        
        #we remove the proposed point from x_new
        dist = np.linalg.norm(x_new - next_one, axis=1)
        min_dist = np.min(dist)

        if min_dist==0:
            mask = dist != np.min(dist)
            x_new = x_new[mask]

        y_i = np.append(y_i, func(next_one))

        #we keep track of the best points (meaning that they maximize the target function) up to now
        best_points[n] = x_i[np.argmax(y_i)]
        values_best_points[n] = max(y_i)


    # and show how we're progressing    
    if show_BO:
        plt.plot(y_i)
        plt.ylabel('y')
        
    # and finally choose the best parameters as the result of the algorithm
    best_x = x_i[np.argmax(y_i)]
    best_y = np.max(y_i)
    
    np.savetxt("ITaI_project_data/" + filename + "_" + kernel_type + "_" + policy + "_" + str(n_BO_iteration) + ".csv", best_points, delimiter=",")
    np.savetxt("ITaI_project_data/values_" + filename + "_" + kernel_type + "_" + policy + "_" + str(n_BO_iteration) + ".csv", values_best_points.T, delimiter=",")
    
    print("All considered points, x_i:", x_i)
    return best_x, best_y

We observe that the number of operations $N_{operations}$ depend on the number of test points examined $n_{new}$ at each iterations and on the dimensionality of the problem $D$ as:
$$ N_{operations} \propto n_{new}^{D}\$$

This exponential dependence limits the optimization to a few quantites at a time, unless more computational resources and/or stratiges are utilized. For this reason and considering our limited computational resources we consider the optimization of 2 parameters. Although in principle the code is applicable to more general cases with more parameters by making a few changes.



### **Testing the performance with benchmark functions** 



We test the performance of the just implemented Bayesian Optimization algorithm [**with benchmark functions**](https://aspuru-guzik-group.github.io/olympus/classes/surfaces/index.html), such as:
- [HyperEllipsoid](https://aspuru-guzik-group.github.io/olympus/classes/surfaces/hyper_ellipsoid.html), with global minima in $\sim [0.5, 0.5]$
  
  <img src="https://aspuru-guzik-group.github.io/olympus/_images/hyper_ellipsoid.png" width="800" align="center"/>

- [Levy](https://aspuru-guzik-group.github.io/olympus/classes/surfaces/levy.html), with global minima in $\sim [0.5, 0.5]$

  <img src="https://aspuru-guzik-group.github.io/olympus/_images/levy.png" width="800" align="center"/>

- [AckleyPath](https://aspuru-guzik-group.github.io/olympus/classes/surfaces/ackley_path.html), with global minima in $\sim [0.5, 0.5]$

  <img src="https://aspuru-guzik-group.github.io/olympus/_images/ackley_path.png" width="800" align="center"/>




In [49]:
def test_points_grid(all_min, all_max, n_new):
    '''
    function that computes a D dimensional grid, corresponding to all possible combination of D 1-D vectors of coordinates
    - the ranges for each of the D dimensions are specified by the all_min and all_max vectors
    - the number of unique coordinates per dimension are specified by n_new
    '''
    D = len(all_min)
    coords = [np.linspace(all_min[j], all_max[j], n_new[j]) for j in range(D)]
    meshgrid_coords = np.meshgrid(*coords, indexing='ij')
    grid = np.vstack([coord.flatten() for coord in meshgrid_coords])
    return grid.T

In [50]:
def opposite(func, x):
    return (-1)*func.run(x)[0][0]

In [51]:
# we initialize
# - the first randomly extracted points to examine
all_min = np.array([0, 0])
all_max = np.array([1, 1])
n0_x_i = 3
x_i = random.uniform(low=all_min, high=all_max, size=(n0_x_i,2))
# - we define the number of samples (and labels) in x_i
N = np.shape(x_i)[0]
# - the dimensionality of each sample in x_i
D = x_i.shape[1]
# - the starting values for the optimization
starting_points = (0.01, 2.0, 0.5, 0.25, 0.125) # 2D
# - the test points to examine, which j-th coordinate takes n_new[j] values from all_min[j] to all_max[j]
n_new = np.array([20, 20])
x_new = test_points_grid(all_min, all_max, n_new)

# we chaeck that x_new instances are not already in x_i
print('x_new shape before checking for elements in x_i:', x_new.shape)
for i in range(n0_x_i):
    dist = np.linalg.norm(x_new - x_i[i], axis=1)
    min_dist = np.min(dist)
    if min_dist==0:
        mask = dist != np.min(dist)
        x_new = x_new[mask]
print('x_new shape after checking for elements in x_i:', x_new.shape)
# - the number of Bayesian Optimization iterations
n_BO_iteration = 50
# - the names of the benchmark functions to examine
filenames = ['Levy', 'HyperEllipsoid', 'AckleyPath']
# - the names of the policies used in BO
policies = ['expected-improvement', 'optimistic']
# - the names of the kernel types used in BO
kernel_types = ['squared-exponential', 'matern-1', 'matern-3', 'matern-5']

# to get all datasets needed later on for the benchmark plots, we run
if FROM_SCRATCH:
    for filename in filenames:
        exec('from olympus.surfaces import '+filename)
        exec('func = lambda x: opposite('+filename+'(), x)')
        # we get the values of the unkown function f in the sample points x_i
        y_i = [func(x_i[i]) for i in range(N)]
        for policy in policies:
            for kernel_type in kernel_types:
                best_x, best_y = bayesian_optimization(policy, x_i, x_new, y_i, kernel_type, starting_points, n_BO_iteration, func, filename)
                print('the optimal parameters resulting from Bayesian optimization are: ', best_x,' and the corresponding value of the target function is: ', best_y)

x_new shape before checking for elements in x_i: (400, 2)
x_new shape after checking for elements in x_i: (400, 2)


In [52]:
def plotting_function(func_name, n_BO_iteration, path='', ylabel='other'):
    '''
    function that plots the already run and saved data relative to all 8 combinations (of kernels and policies) of a specific function.
    the inputs of the function are:
    - the name of the function func_name
    - the number of bayesian iterations used (common to all runs)
    - the coordinates of the known global minimum of the function
    - an option ylabel representing the meaning of the y of the plots (between 'absolute-error', 'accuracy', or 'other', default to other)
    '''
    
    # inside the function
    # we initialize 
    # - all possible kernel and policy types, which we'll need later for the upload
    kernel_types = ['squared-exponential', 'matern-1', 'matern-3', 'matern-5']
    policies = ['expected-improvement', 'optimistic']
    # - the specific colors and markers corresponing to each kernel type (since they will be represented in the same types)
    looks = ['-vm', '-*r', '-ob', '-hg']
    # - the x coordinates common to the plots
    x = np.arange(0, n_BO_iteration, 1)
    # - the figure and axes
    fig, ax = plt.subplots(nrows=1, ncols=2, figsize=(12, 5), dpi=1000)
    # - the vector of maxima of the plot
    maxs_left = np.zeros(len(kernel_types))
    maxs_right = np.zeros(len(kernel_types))
    # - the vector of minima of the plot
    mins_left = np.zeros(len(kernel_types))
    mins_right = np.zeros(len(kernel_types))
    # - the dataframe of best points and max target values
    df = pd.DataFrame()
    df['kernel'] = ['squared-exponential', 'matern-1', 'matern-3', 'matern-5']
    ei_best_points = []
    o_best_points = []
    # we set the same x-lim since the x range is the same
    ax[0].set_title(func_name+' - '+policies[0], fontsize=15)
    ax[1].set_title(func_name+' - '+policies[1], fontsize=15)
    # we iterate over all possible kernel types
    for j in range(len(kernel_types)):
        # for each policy
        ei_name = func_name + '_' + kernel_types[j] + '_' + policies[0] + '_' + str(n_BO_iteration) + '.csv'
        o_name = func_name + '_' + kernel_types[j] + '_' + policies[1] + '_' + str(n_BO_iteration) + '.csv'
        # we load the corresponding file
        ei_y = np.loadtxt(path + 'values_' + ei_name, unpack=True, delimiter=',').T
        ei_points = np.loadtxt(path + ei_name, unpack=True, delimiter=',').T
        o_y = np.loadtxt(path + 'values_' + o_name, unpack=True, delimiter=',').T
        o_points = np.loadtxt(path + o_name, unpack=True, delimiter=',').T
        #
        print()
        ei_best_points.append(np.round(ei_points[np.argmax(ei_y)], 3))
        o_best_points.append(np.round(o_points[np.argmax(o_y)], 3))
        # what's stored is already the best values of the function
        ax[0].plot(x, ei_y, looks[j], label=kernel_types[j])
        ax[1].plot(x, o_y, looks[j], label=kernel_types[j])
        # lastly, we save the maximum and minimum values
        mins_left[j] = np.round(np.min(ei_y), 5)
        maxs_left[j] = np.round(np.max(ei_y), 5)
        mins_right[j] = np.round(np.min(o_y), 5)
        maxs_right[j] = np.round(np.max(o_y), 5)
    
    # we put together the dataframe
    df['ei best point'] = ei_best_points
    df['ei max target value'] = maxs_left
    df['opt best point'] = o_best_points
    df['opt max target value'] = maxs_right
    all_best_points = ei_best_points + o_best_points
    all_max = list(maxs_left) + list(maxs_right)
    best_point = all_best_points[np.argmax(all_max)]
    best_target_value = np.max(all_max)


    # we set the same x limits and x labels
    ax[0].set_xlim(-1, n_BO_iteration)
    ax[1].set_xlim(-1, n_BO_iteration)
    ax[0].set_xlabel('# of BO iterations', fontsize=12)
    ax[1].set_xlabel('# of BO iterations', fontsize=12)
    # we set the same y limits/scales to be able to compare the different policied
    # we use the vector of maximums to find the limits
    width_left = np.max(maxs_left) - np.min(mins_left)
    width_right = np.max(maxs_right) - np.min(mins_right)
    top_left = np.max(maxs_left) + width_left*0.1
    bottom_left = np.min(mins_left) - width_left*0.1
    top_right = np.max(maxs_right) + width_right*0.1
    bottom_right = np.min(mins_right) - width_right*0.1
    ax[0].set_ylim(bottom_left, top_left)
    ax[1].set_ylim(bottom_right, top_right)
    # and set the y labels depending on the option
    if ylabel=='accuracy':
        ax[0].set_ylabel('accuracy', fontsize=12)
        ax[1].set_ylabel('accuracy', fontsize=12)
    else:
        ax[0].set_ylabel('value of the function', fontsize=12)
        ax[1].set_ylabel('value of the function', fontsize=12) 
    # we put legend etc
    ax[1].legend(loc="upper left", ncol=1, fontsize=10, bbox_to_anchor=(1.025, 1.0))
    ax[0].tick_params(axis='both', which='major', labelsize=8)
    ax[1].tick_params(axis='both', which='major', labelsize=8)
    ax[0].grid('minor', alpha=0.5)
    ax[1].grid('minor', alpha=0.5)
    plt.show()
    print('the best point found is: ', best_point, ' and corresponds to the best target function value: ', best_target_value)
    display(df)

In [53]:
func_name = 'HyperEllipsoid'
n_BO_iteration = 50
plotting_function(func_name, n_BO_iteration, path='ITaI_project_data/', ylabel='other')

the best point found is:  [0.526 0.526]  and corresponds to the best target function value:  -0.20776


kernel   ei best point  ei max target value  opt best point  \
0  squared-exponential  [0.526, 0.526]             -0.20776  [0.526, 0.526]   
1             matern-1  [0.526, 0.526]             -0.20776  [0.526, 0.526]   
2             matern-3  [0.526, 0.526]             -0.20776  [0.526, 0.526]   
3             matern-5  [0.526, 0.526]             -0.20776  [0.526, 0.526]   

   opt max target value  
0              -0.20776  
1              -0.20776  
2              -0.20776  
3              -0.20776

In [54]:
func_name = 'Levy'
n_BO_iteration = 50
plotting_function(func_name, n_BO_iteration, path='ITaI_project_data/', ylabel='other')

the best point found is:  [0.526 0.526]  and corresponds to the best target function value:  -0.21502


kernel   ei best point  ei max target value  opt best point  \
0  squared-exponential  [0.526, 0.526]             -0.21502  [0.526, 0.526]   
1             matern-1  [0.526, 0.526]             -0.21502  [0.526, 0.526]   
2             matern-3  [0.526, 0.526]             -0.21502  [0.526, 0.526]   
3             matern-5  [0.526, 0.526]             -0.21502  [0.526, 0.526]   

   opt max target value  
0              -0.21502  
1              -0.21502  
2              -0.21502  
3              -0.21502

In [55]:
func_name = 'AckleyPath'
n_BO_iteration = 50
plotting_function(func_name, n_BO_iteration, path='ITaI_project_data/', ylabel='other')

the best point found is:  [0.568 0.596]  and corresponds to the best target function value:  -6.23233


kernel   ei best point  ei max target value  opt best point  \
0  squared-exponential  [0.568, 0.596]             -6.23233  [0.468, 0.326]   
1             matern-1  [0.474, 0.474]             -7.76867  [0.568, 0.596]   
2             matern-3  [0.568, 0.596]            -14.65882  [0.749, 0.654]   
3             matern-5  [0.568, 0.596]            -14.65882  [0.299, 0.656]   

   opt max target value  
0             -16.67225  
1             -14.65882  
2             -19.30926  
3             -18.34136

As we can see from the three plots above, there is no single perfect recipe for all functions. 

For Levy and Hyperellipsoid, we notice that:
- the final results are reached by all combinations of policies and kernels, but with varying number of BO iterations
- the optimistic policy starts examining from further points, but is also more likely to change for a better value
- the expected improvement policy starts closer to the final output, but changes less

These tendencies are likely to be related to the smoother shape of the functions.

For AckleyPath, we clearly see from the plots that both policies get stuck in different local maxima, because of the very complicated shape of the function.

## **Applying BO to machine learning**

### **Defining the ML model**





For testing the implemented Bayesian optimization algorithm we consider a simple neural network on the MNIST dataset.

MNIST dataset is a dataset of handwritten diigits, containing 60,000 training images and 10,000 testing images. The labels are digits 0-9.

As an architecture for a neural network we take a convolutional neural network with one convolution layer, one max pooling layer and a fully connected layer with the output predicting one of the 10 labels.

In [56]:
def load_and_prepare_dataset(show=False):
    '''
    function that loads the MNIST dataset, reshapes the data,
    one-hot encodes the labels
    
    with show=True prints 4 examples of the dataset
    '''
    
    (X_train, Y_train), (X_test, Y_test) = mnist.load_data()
    
    #show first four entries of the training data
    if show:
        for i in range(4):  
            plt.subplot(330 + 1 + i)
            plt.imshow(X_train[i], cmap=plt.get_cmap('gray'))
            plt.tight_layout()
            plt.show()
            
    X_train = X_train.reshape((X_train.shape[0], 28, 28, 1)).astype('float32')/255.0
    X_test = X_test.reshape((X_test.shape[0], 28, 28, 1)).astype('float32')/255.0
    
    Y_train = to_categorical(Y_train)
    Y_test = to_categorical(Y_test)
    
    return X_train, Y_train, X_test, Y_test

In [57]:
X_train, Y_train, X_test, Y_test = load_and_prepare_dataset()

Here we define a function with the CNN, that takes as inputs the learning rate and the momentum, which are used in the stochastic gradient descent. Optimal values for these parameters will be found via bayesian optimization.

In [58]:
def CNN(parameters):
    '''
    function that defines CNN
    input: array [learning rate, momentum]
    '''
    model = Sequential()
    model.add(Conv2D(32, (3, 3), activation='relu', input_shape=(28, 28, 1)))
    model.add(MaxPooling2D((2, 2)))
    model.add(Flatten())
    model.add(Dense(10, activation='softmax'))
    
    optimizer = SGD(learning_rate = parameters[0], momentum = parameters[1])
    model.compile(optimizer = optimizer,
                  loss = 'categorical_crossentropy',
                  metrics=['accuracy'])
    return model
    
def model_accuracy(X_train, Y_train, X_test, Y_test, parameters, num_epoch):
    '''
    function that returns ML model's accuracy
    input: train/test datasets, parameters [learning rate, momentum], number of epochs
    output: accuracy on the test set
    '''

    model = CNN(parameters)
    model.fit(X_train, Y_train, epochs=num_epoch, batch_size=32, verbose=0)
    _, accuracy = model.evaluate(X_test, Y_test)
        
    return accuracy

In the bayesian optimization context our parameters are learning rate and momentum, the "unknown function $f$" is the accuracy of the CNN.

In order to put the parameters into the bayesian optimization algorithm, we firstly train CNN with chosen values of parameters, so that we obtain initial data pairs. After we can propose a set of new potential points and run the bayesian optimization.

In [59]:
learning_rates = [0.01, 0.05]
momenta = [0.9, 0.5]

#make all possible pairs of [learning_rate, momenta]
#these are initial points
parameters = [[a, b] for _,a in enumerate(learning_rates) for _,b in enumerate(momenta)]

If we already trained the CNN before and saved the results to a file, we can just read this file.
Otherwise we start trainig the CNN and save the results into a file.

In [60]:
accuracy = np.zeros(len(parameters))
nepoch = 10
if not FROM_SCRATCH:
    accuracy = np.genfromtxt('ITaI_project_data/accuracyML_10.csv', delimiter=',')
else:
    for i in range(len(accuracy)):
        accuracy[i] = model_accuracy(X_train, Y_train, X_test, Y_test, parameters[i], 20)
    np.savetxt("ITaI_project_data/accuracyML_10.csv", accuracy.T, delimiter=",")
accuracy

array([0.98360002, 0.97960001, 0.98250002, 0.98180002])

Now we make a new list of parameters, that is considered as a set of new possible points.

In [61]:
learning_rates2 = list(np.round(np.linspace(0.001, 0.09, 10),3))
momenta2 = list(np.round(np.linspace(0.1, 0.9, 10),2))

#make all possible pairs of [learning_rate, momenta]
parameters_duplicated = [[a, b] for _,a in enumerate(learning_rates2) for _,b in enumerate(momenta2)]

#remove points that were already considered before
parameters_new = [a for a in parameters_duplicated if a not in parameters]

### **Finding the optimal ML hyperparameters**


In [62]:
x_i = np.array(parameters)
# - we define the number of samples (and labels) in x_i
N = np.shape(x_i)[0]
# - the values of the unkown function f in the sample points x_i
y_i = np.array(accuracy)
#new proposed points
x_new = np.array(parameters_new)
# - the starting values for the optimization
starting_points = (0.1, 2.0, 0.5, 0.25, 0.125) # 2D
# - the number of Bayesian Optimization iterations
n_BO_iteration = 50
# - the filename
filename = 'CNN'
# - the names of the policies used in BO
policies = ['expected-improvement', 'optimistic']
# - the names of the kernel types used in BO
kernel_types = ['squared-exponential', 'matern-1', 'matern-3', 'matern-5']
# - the number of epochs
nepochs = 10

# we build a helping function in order to pass the objective function to the bayesian optimization algorithm.
def CNN_func_for_BO(parameters):
    return model_accuracy(X_train, Y_train, X_test, Y_test, parameters, nepochs)

# to produce the files for the following plots:
if FROM_SCRATCH:
    for kernel_type in kernel_types:
        for policy in policies:
            best_x, best_y = bayesian_optimization(policy, x_i, x_new, y_i, kernel_type, starting_points, n_BO_iteration, CNN_func_for_BO, 'CNN')
            print('the optimal parameters resulting from Bayesian optimization are: ', best_x,' and the corresponding accuracy is: ', best_y)

In [63]:
func_name = 'CNN'
n_BO_iteration = 50
plotting_function(func_name, n_BO_iteration, path='ITaI_project_data/', ylabel='other')

the best point found is:  [0.09 0.63]  and corresponds to the best target function value:  0.9859


kernel ei best point  ei max target value opt best point  \
0  squared-exponential  [0.07, 0.72]               0.9851   [0.09, 0.72]   
1             matern-1  [0.08, 0.81]               0.9852   [0.09, 0.54]   
2             matern-3  [0.06, 0.72]               0.9853   [0.08, 0.63]   
3             matern-5  [0.09, 0.63]               0.9859   [0.09, 0.72]   

   opt max target value  
0                0.9854  
1                0.9849  
2                0.9847  
3                0.9859

We notice from the plots that, for our CNN application, the matern-5 kernel seems to be optimal for both policies. The resulting accuracy is more than acceptable.

## **Comparing the results of out BO with built-in methods**


Lastly, we compare the results obtained with our Bayesian optimization algorithm with similar packages tools:
- [Keras Tuner](https://keras.io/keras_tuner/) provides multiple algorithm choices, including a Bayesian Optimization one.

- the [Bayesian optimization package](https://github.com/bayesian-optimization/BayesianOptimization)

In [64]:
import keras_tuner as kt

# firstly, we need to adapt our model function to this specific optimization tool's syntax
def kt_model(hp):
    parameters = np.zeros(2)
    parameters[0] = hp.Float('parameters[0]',
                              min_value=0.001,
                              max_value=0.09,
                              step=(0.09-0.001)/(10-1),
                              sampling='linear',
                              )
    parameters[1] = hp.Float('parameters[1]',
                              min_value=0.01,
                              max_value=0.9,
                              step=(0.09-0.001)/(10-1),
                              sampling='linear'
                              )

    model = CNN(
        parameters=parameters)
    return model

# we check that the adaptation of the model works (i.e. has keras tuner's hyperparameter class)
kt_model(kt.HyperParameters())

C:\Users\ecica\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\keras\src\layers\convolutional\base_conv.py:99: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(


<Sequential name=sequential_1, built=True>

In [65]:
# for Keras Tuner's BayesianOptimization
if FROM_SCRATCH:
    kt_BO_tuner = kt.BayesianOptimization(hypermodel=kt_model,
                                        objective='val_accuracy',
                                        overwrite=True,
                                        seed=seed,
                                        max_trials=50
                                            )

    kt_BO_tuner.search_space_summary()
    kt_BO_tuner.search(X_train, Y_train, epochs=10, validation_data=(X_test, Y_test))
    best_hp_BO = kt_BO_tuner.get_best_hyperparameters()
    best_model_BO = kt_BO_tuner.get_best_models(num_models=1)
    _, test_acc = best_model_BO[0].evaluate(X_test, Y_test)
    temp = np.array([best_hp_BO[0].values['parameters[0]'], best_hp_BO[0].values['parameters[1]'], test_acc])
    np.savetxt('keras_tuner_BO_best_params.txt', temp, delimiter=",")
    print('for keras tuner BO \n','the best point found is: ', temp[0:2], ' and corresponds to the best target function value: ', temp[2])
else:
    temp = np.loadtxt('keras_tuner_BO_best_params.txt', unpack=True, delimiter=',')
    print('for keras tuner BO \n','the best point found is: ', temp[0:2], ' and corresponds to the best target function value: ', temp[2])

for keras tuner BO 
 the best point found is:  [0.03066667 0.9       ]  and corresponds to the best target function value:  0.9854999780654907


In [66]:
from bayes_opt import BayesianOptimization
from bayes_opt import UtilityFunction

if FROM_SCRATCH:
    # we adapt our ML functions to the syntax of the package
    def CNN_for_BO_package(x, y):
        parameters = np.array([x,y])
        return CNN_func_for_BO(parameters)

    # we specify the number of iterations
    n_BO_iteration = 50
    # and type of optimizer
    optimizer = BayesianOptimization(
        f=CNN_for_BO_package,
        pbounds={'x': (0.001, 0.9), 'y': (0.01, 0.9)},
        random_state=seed
    )

    utility = UtilityFunction(kind="ei") #ucb for optimistic, ei for expected improvement

    for _ in range(n_BO_iteration):
        next_point = optimizer.suggest(utility)
        target = CNN_for_BO_package(**next_point)
        optimizer.register(params=next_point, target=target)
    
    temp = np.array([optimizer.max['params']['x'], optimizer.max['params']['y'], optimizer.max['target']])
    np.savetxt('BO_package_ei_best_params.txt', temp, delimiter=",")
    print('for BO package \n','the best point found is: ', temp[0:2], ' and corresponds to the best target function value: ', temp[2])
else:
    temp = np.loadtxt('BO_package_ei_best_params.txt', unpack=True, delimiter=',')
    print('for BO package \n','the best point found is: ', temp[0:2], ' and corresponds to the best target function value: ', temp[2])
    


for BO package 
 the best point found is:  [0.21609108 0.07720586]  and corresponds to the best target function value:  0.9857000112533569


We notice that the comparable tools reach similar results in terms of accuracy, in similar amounts of time as our algorithm.

## **Conclusions**

After implementing our Bayesian optimization algorithm, we applied it to 3 different benchmark functions to test its performance with different combinations of policies and kernels.
We notices that there are limits to the optimization that are dictated by the complexity of the function. 

Since we noticed that there wasn't an overall optimal combination, we implemented a CNN and displayed the results still for different combinations of policies and kernels, to identify the best one for our particular case.
We found that, for our specific CNN and dataset, the best performing kernel was matern-5, for both expected-improvement and optimistic policy.

We finally compared the results obtained with our Bayesian optimization algorithm, to some equivalent tools from python packages. We found that our algorithm is comparable with such tools, both in terms of time and accuracy, reaching an even slightly higher accuracy .

## **Sources**

[1] [Shahriari, B., Swersky, K., Wang, Z., Adams, R. P., & de Freitas, N. (2015, December 18). Taking the human out of the loop: A review of Bayesian optimization]( https://ieeexplore.ieee.org/document/7352306/ )

[2] [Snoek, J., Larochelle, H., & Adams, R. P. (2012, August 29). Practical Bayesian optimization of Machine Learning Algorithms](https://arxiv.org/abs/1206.2944) 

[3] [Peter I. Frazier (2018, July 10) A Tutorial on Bayesian Optimization](https://arxiv.org/pdf/1807.02811.pdf)
